# Comparing statistics of NO2 pollution for American States

In [ ]:
%matplotlib inline

In [ ]:
import numpy as np

In [ ]:
from pathlib import Path
import getpass

import matplotlib.pyplot as plt
import seaborn as sns
import numpy as np
import pandas as pd
import geopandas as gpd
import rasterio
import rasterio.plot
from rasterio import features

from sentinelhub import (
    SHConfig,
    CRS,
    BBox,
    DataCollection,
    DownloadRequest,
    MimeType,
    MosaickingOrder,
    SentinelHubDownloadClient,
    SentinelHubStatisticalDownloadClient,
    SentinelHubRequest,
    bbox_to_dimensions,
    SentinelHubStatistical,
    Geometry,
    parse_time,
)

In [ ]:
!pip install ffmpeg

In [ ]:
import matplotlib.pyplot as plt
import numpy as np
import ffmpeg


# Measuring NO2 concentrations

In [ ]:
config = SHConfig()
config.sh_client_id = getpass.getpass("sh-786e6f87-83ac-4efd-88d2-a7348d9d88b6")
config.sh_client_secret = getpass.getpass("co0KzMk9afDfz6PoyfURllx5pIr9Bw34")
config.sh_token_url = "https://identity.dataspace.copernicus.eu/auth/realms/CDSE/protocol/openid-connect/token"
config.sh_base_url = "https://sh.dataspace.copernicus.eu"
config.save("abinaya-dinesh")

In [ ]:
config = SHConfig("abinaya-dinesh")

### Analysing Spatial Distribution

In [ ]:
bbox_america = BBox([-125.0, 24.0, -66.934570, 49.384358], crs=CRS.WGS84).transform(CRS(3857))
bbox_europe = BBox([-12.30, 34.59, 32.52, 63.15], crs=CRS.WGS84).transform(CRS(3857))
bbox_iowa = BBox([-96.558652, -90.748320, 40.620395, 43.480644], crs=CRS.WGS84).transform(CRS(3857))
bbox_vermont = BBox([-73.388769,-71.521093,42.802392, 45.002621], crs=CRS.WGS84).transform(CRS(3857))

data_5p = DataCollection.SENTINEL5P.define_from("5p", service_url=config.sh_base_url)

In [ ]:
states = (
    gpd.read_file("./data_america/ne_50m_admin_1_states_provinces.shp")
    .to_crs(3857)
    .cx[bbox_america.min_x : bbox_america.max_x, bbox_america.min_y : bbox_america.max_y]
    .reset_index(drop=True)
)
states = states[["name", "geometry"]]

In [ ]:
names = states["name"] #returns a pandas series from a geodataframe
names[0]

Define an evalscript: a piece of javascript code which specifies how each pixel should be handled. For the first one we just define the input band that we want to look at, which is `NO2` and return that band immediately, without carrying out any more calculations before the data is returned to us.


In [ ]:
evalscript_raw_NO2 = """
//VERSION=3
function setup() {
   return {
    input: ["NO2"], // This specifies the bands that are looked at
    output: { 
      bands: 1,
      // This specifies in which data type the values will be returned
      sampleType: "FLOAT32"
    },
    // Will make a simple mosaic, taking the most recent tiles to fill the bounding box
    mosaicking: "SIMPLE"
  };
}

function evaluatePixel(samples) {
    // Here we could do more calculations which are applied to each pixel, 
    // but for now let's just return the value 
   return [samples.NO2] 
}
"""

In [ ]:
from matplotlib.animation import FFMpegWriter
metadata = dict(title='NO2 Concentrations Over 5 Years in America', artist='Matplotlib',comment='')
writer = FFMpegWriter(fps=15, metadata=metadata)
fig = plt.figure()

def define(start_interval, end_interval):
    return SentinelHubRequest(
    evalscript=evalscript_raw_NO2,
    input_data=[
        SentinelHubRequest.input_data(
            data_collection=data_5p,
            time_interval=(start_interval, end_interval),
        )
    ],
    responses=[SentinelHubRequest.output_response("default", MimeType.TIFF)],
    bbox=bbox_america,
    # Resolution is defined in units of the bbox crs! Be careful with WGS84 since this will be in degrees!
    # Since we have defined our bounding box in Web mercator the resolution is in meters.
    resolution=(5500, 3500),
    config=config,
    data_folder="./data_america",  # We save the data in a specified folder
)

years = ["2021", "2022", "2023"]
months = ["01","02","03","04","05","06","07","08","09","10","11","12"]


with writer.saving(fig, "no2changes.mp4", dpi=200):
    for year in range(0, len(years)):
        for month in range(0, len(months)):
            if year == 2 and month == 11:
                break
            if month == 11 and year < 2:
                interval_start = years[year] + "-" + months[month] + "-" +"01"  
                interval_end = years[year+1] + "-" + "01" + "-" +"01" 
            else:
                interval_start = years[year] + "-" + months[month] + "-" + "01"  
                interval_end = years[year] + "-" + months[month+1] + "-" + "01" 
            request_raw_NO2_america = define(interval_start, interval_end)
            raw_data = request_raw_NO2_america.get_data(save_data=True)
    
            # PLOT IT
            print(years[year], months[month])
            image_path = Path(request_raw_NO2_america.data_folder) / request_raw_NO2_america.get_filename_list()[0]
            with rasterio.open(image_path) as raster:
                fig, ax = plt.subplots(figsize=(10, 10))
                ax.set_xlim([bbox_america.min_x, bbox_america.max_x])
                ax.set_ylim([bbox_america.min_y, bbox_america.max_y])
                rasterio.plot.show(raster, ax=ax)
                states.plot(ax=ax, facecolor="none", edgecolor="black")
                plt.title("NO2 Concentrations in America from " + interval_start + " to " + interval_end)
                plt.savefig("./figures")
                plt.show()
                plt.draw()
                plt.pause(0.05)
                writer.grab_frame()
                plt.close(fig)